In [1]:
import pandas as pd
import geopandas as gpd
import subprocess
import numpy as np
import shapely.geometry as shpg
from shapely.ops import linemerge
from shapely import set_precision
import os
import sys
import csv
import json
import logging
import shutil
import utm

In [2]:
import warnings
warnings.filterwarnings('ignore', category=FutureWarning)

In [3]:
sys.path.append(os.getcwd() + '/../..')
from utils import mkdir, open_zip_shapefile, open_tar_shapefile, haversine, correct_geoms, fix_overaps

In [4]:
log = logging.getLogger('papermill')
logging.basicConfig(level='INFO', format="%(message)s")

## Files and storage paths

In [5]:
# go down from rgi7_scripts/workflow
data_dir = '../../../../rgi7_data/'

# Input dirctory
input_dir = os.path.join(data_dir, 'rgi7_final/regional_files/RGI2000-v7.0-G/')

# Output directories
output_dir = mkdir(os.path.join(data_dir, 'rgi7_rgi6_links'))
output_dir_zip = mkdir(os.path.join(data_dir, 'rgi7_rgi6_links_zip'))

In [6]:
# RGI v6 file for comparison later 
rgi6_files = {
    '01': '01_rgi60_Alaska.zip',
    '02': '02_rgi60_WesternCanadaUS.zip',
    '03': '03_rgi60_ArcticCanadaNorth.zip',
    '04': '04_rgi60_ArcticCanadaNorth.zip',
    '05': '05_rgi60_GreenlandPeriphery.zip',
    '06': '06_rgi60_Iceland.zip',
    '07': '07_rgi60_Svalbard.zip',
    '08': '07_rgi60_Scandinavia.zip',
    '09': '09_rgi60_RussianArctic.zip',
    '10': '10_rgi60_NorthAsia.zip',
    '11': '11_rgi60_CentralEurope.zip',
    '12': '12_rgi60_CaucasusMiddleEast.zip',
    '13': '13_rgi60_CentralAsia.zip',
    '14': '14_rgi60_SouthAsiaWest.zip',
    '15': '15_rgi60_SouthAsiaEast.zip',
    '16': '16_rgi60_LowLatitudes.zip',
    '17': '17_rgi60_SouthernAndes.zip',
    '18': '18_rgi60_NewZealand.zip',
    '19': '19_rgi60_AntarcticSubantarctic.zip',
}

### Load the input data

In [7]:
from utils import open_zip_shapefile

In [8]:
shp = []
rgi6 = []
for reg in range(1, 20):
    reg_str = f'{reg:02d}'
    rgi6_reg_file = os.path.join(data_dir, 'l0_RGIv6', rgi6_files[reg_str])
    
    reg_file = os.path.join(data_dir, '00_rgi70_regions', '00_rgi70_O1Regions')
    reg_file = gpd.read_file(reg_file)
    reg_file = reg_file.loc[reg_file.o1region == f'{reg:02d}'].iloc[0]

    input_regfile = f'{input_dir}/RGI2000-v7.0-G-{reg_file.long_code}.zip'
    
    # Read files
    shp.append(open_zip_shapefile(input_regfile))
    rgi6.append(open_zip_shapefile(rgi6_reg_file))
shp = pd.concat(shp)
rgi6 = pd.concat(rgi6)

## Links to RGI6

In [9]:
import overlaps_helpers

In [10]:
# Compute RGI7 - RGI6 overlaps
overlaps = overlaps_helpers.compute_cross_overlaps(shp.geometry, rgi6.geometry)

Finding intersecting geometries
Computing overlap of intersecting pairs


In [11]:
# Add more stats
overlaps['area_km2'] = overlaps['geometry'].to_crs({'proj':'cea'}).area * 1e-6
overlaps['i'] = shp['rgi_id'].iloc[overlaps['i']].values
overlaps['j'] = rgi6['RGIId'].iloc[overlaps['j']].values

In [12]:
# Filter by minimum area. See https://github.com/ezwelty/rgi_links/issues/6
overlaps_unfiltered = overlaps.copy()
print(len(overlaps_unfiltered))
overlaps = overlaps[overlaps['area_km2'] > (200 * 1e-6)].copy()
print(len(overlaps))

380795
298256


In [22]:
overlaps_unfiltered.area_km2.sum(), overlaps.area_km2.sum(), overlaps.area_km2.sum() - overlaps_unfiltered.area_km2.sum()

(686151.6935762381, 686150.5365909796, -1.156985258567147)

In [13]:
# Count number of direct relatives (i.e. 1:1, n:1, 1:n, n:n)
overlaps['in'], overlaps['jn'] = overlaps_helpers.count_pair_relations(
  overlaps['i'], overlaps['j']
)
# Label clusters of (directly and indirectly-related) pairs
overlaps['cluster'] = overlaps_helpers.label_pair_clusters(overlaps['i'], overlaps['j'])

In [14]:
# Remove geometry for now
odf_links = overlaps[['i', 'j', 'area_km2', 'i_area_fraction', 'j_area_fraction', 'cluster', 'in', 'jn']].copy()
odf_links.columns = ['rgi7_id', 'rgi6_id', 'overlap_area_km2', 'rgi7_area_fraction', 'rgi6_area_fraction', 'cluster_id', 'n_rgi7', 'n_rgi6']

In [15]:
odf_links;

### Check regions 

In [16]:
odf_links['rgi7_reg'] = [r.split('-')[3] for r in odf_links.rgi7_id]
odf_links['rgi6_reg'] = [r.split('-')[1].split('.')[0] for r in odf_links.rgi6_id]

In [17]:
odf_links = odf_links[['rgi7_id', 'rgi6_id', 'rgi7_reg', 'rgi6_reg', 'overlap_area_km2', 'rgi7_area_fraction', 'rgi6_area_fraction', 'cluster_id', 'n_rgi7', 'n_rgi6']].copy()

In [18]:
odf_links.loc[odf_links['rgi7_reg'] != odf_links['rgi6_reg']]

rgi7_id         rgi6_id rgi7_reg rgi6_reg  \
43714   RGI2000-v7.0-G-01-24038  RGI60-02.11256       01       02   
43763   RGI2000-v7.0-G-01-24070  RGI60-02.11242       01       02   
43801   RGI2000-v7.0-G-01-24092  RGI60-02.11003       01       02   
52161   RGI2000-v7.0-G-02-01236  RGI60-01.05285       02       01   
52174   RGI2000-v7.0-G-02-01246  RGI60-01.23371       02       01   
...                         ...             ...      ...      ...   
326635  RGI2000-v7.0-G-15-12200  RGI60-13.25442       15       13   
326639  RGI2000-v7.0-G-15-12201  RGI60-13.25442       15       13   
326733  RGI2000-v7.0-G-15-12292  RGI60-13.29172       15       13   
326735  RGI2000-v7.0-G-15-12293  RGI60-13.29172       15       13   
332725  RGI2000-v7.0-G-15-17323  RGI60-13.25451       15       13   

        overlap_area_km2  rgi7_area_fraction  rgi6_area_fraction  cluster_id  \
43714           0.000289            0.000064            0.003122       23300   
43763           0.000658            0.000685            0.001128       23332   
43801           0.000252            0.001541            0.000145       23354   
52161           0.419305            0.992972            0.992972       28002   
52174           0.000208            0.000193            0.001201       23371   
...                  ...                 ...                 ...         ...   
326635          0.049426            0.030431            0.084043      121354   
326639          0.000395            0.000606            0.000672      121354   
326733          0.025628            0.380432            0.034289      121377   
326735          0.018463            0.062159            0.024704      121377   
332725          0.133862            0.218158            0.125537      121355   

        n_rgi7  n_rgi6  
43714        2       2  
43763        2       2  
43801        2       2  
52161        1       1  
52174        2       2  
...        ...     ...  
326635       5       4  
326639       5       4  
326733       5       2  
326735       5       2  
332725       2       3  

[325 rows x 10 columns]

In [19]:
odf_links.loc[odf_links['rgi7_reg'] != odf_links['rgi6_reg']].overlap_area_km2.sum()

197.47861653863202

In [24]:
odf_links.loc[odf_links['rgi7_reg'] != odf_links['rgi6_reg']].groupby('rgi7_reg').overlap_area_km2.sum()

rgi7_reg
01     0.001199
02     0.420721
13    68.783294
14    52.091768
15    76.181634
Name: overlap_area_km2, dtype: float64

### Write out

In [23]:
print('Writing...')
odf_links.to_csv(output_dir + f'/RGI2000-v7.0-G-global-rgi6_links.csv', quoting=csv.QUOTE_NONNUMERIC, index=False)

for reg in range(1, 20):
    reg_str = f'{reg:02d}'
    reg_file = os.path.join(data_dir, '00_rgi70_regions', '00_rgi70_O1Regions')
    reg_file = gpd.read_file(reg_file)
    reg_file = reg_file.loc[reg_file.o1region == f'{reg:02d}'].iloc[0]
    odf_links.loc[odf_links.rgi7_reg == reg_str].to_csv(output_dir + f'/RGI2000-v7.0-G-{reg_file.long_code}-rgi6_links.csv', 
                                                        quoting=csv.QUOTE_NONNUMERIC, index=False)

Writing...
